In [33]:
import requests
from datetime import datetime, timedelta
from datetime import time
from zk import ZK, const
import pandas as pd

In [34]:
def get_dates(attendances):
    dates = []
    for item in attendances:
        splitted_attendance = str(item).split()
        dates.append(datetime.strptime(splitted_attendance[3], '%Y-%m-%d'))
    max_date = max(dates)
    # dates.sort( reverse = True)
    temp_dates = []
    for i in range(1,4):
        temp_dates.append((max_date - timedelta(days = i)).date())
    temp_dates.sort()
    
    punch_date_list = []
    for item in temp_dates:
        punch_date_list.append(str(item))
    punch_date_list.append(str(max_date.date()))
    
    return punch_date_list    

In [35]:
def get_attendance_logs(attendances, punch_date_list):
    attendance_list = []
    #print(attendances)
    biometric_id_list = []
    for i in attendances:    
        splitted_attendance = str(i).split()   
        #punch_date_list.append(splitted_attendance [3])
        biometric_id_list.append(splitted_attendance [1])
        attendance_list.append(splitted_attendance)

    # punch_date_list = list(set(punch_date_list))
    biometric_id_list = list(set(biometric_id_list))
    #print (attendance_list) 

    attendance_logs = []


    for id in biometric_id_list:
        for date in punch_date_list:
            log_list = []
            log_list.append(id)
            log_list.append(date)
            punch_time = []        
            for attendance in attendance_list:
                #print (attendance[3], date)
                if attendance[1] == id and attendance[3] == date:
                    time = datetime.strptime(attendance[3]+" "+attendance[4],'%Y-%m-%d %H:%M:%S')
                    # time2 = datetime(2022, 10, 19, 4, 1, 30, 00)
                    # log_list.insert(2, attendance[4])
                    punch_time.append(str(time))
                    # punch_time.append(str(time2))
            if punch_time:
                log_list.append(str(punch_time))
                # log_list.append(str(max(punch_time)))
            if len(log_list) >= 3:
                attendance_logs.append(log_list)
            else:
                continue
    return attendance_logs
    #print(log_list)
    #print(attendance_logs)

In [36]:
def get_access_token():
    url = 'http://127.0.0.1:8000/attendance-log/api/token/'
    headers = {"Content-Type": "application/json; charset=utf-8"
                   
              }

    data = {
        "username": 'admin',
        "password": 1234,
    }
    response = requests.post(url, headers=headers, json=data)

    return response.json()['access']

In [37]:
def create_post_request(device_id,file):
    token = get_access_token()
    url = 'http://127.0.0.1:8000/attendance-log/api/check-in/'
    headers = {
               "Authorization": "Bearer "+token
               
              }

    data = {
        
        "device_id": device_id,
             
    } 
    response = requests.post(url, headers=headers,data=data,files = {"text_file": file })



    print("Status Code", response.status_code)
    print("JSON Response ", response.json())

In [38]:
zk = ZK('10.10.1.25', port=4380, timeout=5, password=0, force_udp=False, ommit_ping=False)
try:
    #connect to device
    conn = zk.connect()
    conn.disable_device()  
    attendances = conn.get_attendance()
    punch_date_list = get_dates(attendances)
    attendance_logs = get_attendance_logs(attendances, punch_date_list)
    # df = pd.DataFrame(attendance_logs,columns=['biometric_id','date','punch_list'])
    
    
    
except Exception as e:
    print ("Process terminate : {}".format(e))
finally:
    if conn:
        conn.disconnect()

In [39]:
# create_post_request('ODELLHEADOFFFICE', open("machine_attendance3.txt", "r"))

In [42]:
import os
if os.path.exists("machine_attendance3.txt"):
      os.remove("machine_attendance3.txt")


with open('machine_attendance3.txt', 'w') as f:
        # for item in attendance_logs:
        #     for log in item:
        #         f.write("%s\n" % item)
        #         # f.write(log)
        for item in attendance_logs:
            
                f.write("%s\n" % item)
                # f.write(log)
                
        


In [82]:
# f = open("machine_attendance3.txt", "r")
create_post_request('ODELLHEADOFFFICE', open("machine_attendance3.txt", "r"))



Status Code 201
JSON Response  {'id': 68, 'device_id': 'ODELLHEADOFFFICE', 'text_file': 'http://127.0.0.1:8000/media/attendance/machine_attendance3_lcFZKUF.txt'}


In [12]:
print(f)

<_io.TextIOWrapper name='machine_attendance3.txt' mode='r' encoding='UTF-8'>


In [14]:
log_list = []
with open("machine_attendance3.txt", "r") as file:
    while (line := file.readline().rstrip()):
        log_list.append(line)

In [21]:
log_list[0]

'[\'103\', \'2022-10-24\', "[\'2022-10-24 10:33:22\']"]'

In [ ]:
# for item in punch_time:
#             item = item.translate({ord(i): None for i in "'[]'"}).lstrip()
#             item = datetime.datetime.strptime(item,'%Y-%m-%d %H:%M:%S')
#             time_list.append(item)

In [37]:
item = log_list[40].translate({ord(i): None for i in "'[]'"}).lstrip()

In [38]:
item = item.split(',')
item

['101',
 ' 2022-10-23',
 ' "2022-10-23 07:30:48',
 ' 2022-10-23 07:59:07',
 ' 2022-10-23 21:55:06"']

In [41]:
date = item[1].strip()

In [43]:
date = datetime.strptime(date,'%Y-%m-%d')

In [48]:
biometric_id = int(item[0])

In [55]:
punch_time = item[2]


In [57]:
punch_time = punch_time.split(',')

In [63]:
for item in punch_time:
            item = item.translate({ord(i): None for i in "'[]'"}).lstrip()
            item = item.replace('"','')
            item = datetime.strptime(item,'%Y-%m-%d %H:%M:%S')
            # time_list.append(item)

In [64]:
log_list = []
with open("machine_attendance3.txt", "r") as file:
    while (line := file.readline().rstrip()):
        log_list.append(line)

In [69]:
for log in log_list:
    log = log.translate({ord(i): None for i in "'[]'"}).lstrip()
    log = log.split(',')
    date =log[1].strip()
    date = datetime.strptime(date,'%Y-%m-%d') 
    biometric_id = int(log[0])
    punch_time = log[2]
    punch_time = punch_time.split(',')   
    for item in punch_time:
            item = item.translate({ord(i): None for i in "'[]'"}).lstrip()
            item = item.replace('"','')
            item = datetime.strptime(item,'%Y-%m-%d %H:%M:%S')
            print(item)
            # time_list.append(item)
   

2022-10-24 10:33:22
2022-10-24 10:33:22
2022-10-24 10:33:22
2022-10-25 10:49:33
2022-10-25 10:49:33
2022-10-25 10:49:33
2022-10-26 10:05:46
2022-10-26 10:05:46
2022-10-26 10:05:46
2022-10-24 08:54:00
2022-10-24 08:54:00
2022-10-24 08:54:00
2022-10-25 09:09:03
2022-10-25 09:09:03
2022-10-25 09:09:03
2022-10-23 11:10:05
2022-10-23 11:10:05
2022-10-23 11:10:05
2022-10-24 14:03:54
2022-10-24 14:03:54
2022-10-24 14:03:54
2022-10-25 09:37:22
2022-10-25 09:37:22
2022-10-25 09:37:22
2022-10-26 09:47:35
2022-10-26 09:47:35
2022-10-26 09:47:35
2022-10-23 11:09:41
2022-10-23 11:09:41
2022-10-23 11:09:41
2022-10-24 10:50:19
2022-10-24 10:50:19
2022-10-24 10:50:19
2022-10-25 09:38:33
2022-10-25 09:38:33
2022-10-25 09:38:33
2022-10-26 10:09:00
2022-10-26 10:09:00
2022-10-26 10:09:00
2022-10-23 07:30:48
2022-10-23 07:30:48
2022-10-23 07:30:48
2022-10-24 08:19:18
2022-10-24 08:19:18
2022-10-24 08:19:18
2022-10-25 07:24:54
2022-10-25 07:24:54
2022-10-25 07:24:54
2022-10-26 07:21:58
2022-10-26 07:21:58
